In [1]:
import os
import pandas as pd

In [2]:
train_set = pd.read_csv(os.path.join(os.getcwd(), 'train.csv'))

In [3]:
df = train_set.loc[train_set.Embarked.notna(), ['Survived', 'Pclass']]

In [4]:
df.shape

(889, 2)

In [5]:
X = df.loc[:, ['Pclass']]

In [6]:
y = df.Survived

In [7]:
X.shape

(889, 1)

In [8]:
y.shape

(889,)

In [9]:
from sklearn.linear_model import LogisticRegression

In [10]:
logreg = LogisticRegression(solver='lbfgs', max_iter=10000)

In [11]:
from sklearn.model_selection import cross_val_score, GridSearchCV

In [12]:
scoring = ['accuracy', 'precision', 'recall', 'roc_auc']

In [13]:
import numpy as np
from sklearn.ensemble import RandomForestClassifier

In [14]:
param_grid = [
    {'classifier' : [LogisticRegression()],
     'classifier__penalty' : ['l1', 'l2'],
    'classifier__C' : np.logspace(-4, 4, 20),
    'classifier__solver' : ['liblinear']},
    {'classifier' : [RandomForestClassifier()],
    'classifier__n_estimators' : list(range(10,101,10)),
    'classifier__max_features' : list(range(6,32,5))}
]

In [15]:
from sklearn.model_selection import cross_validate

In [16]:
cross_validate(logreg, X, y, scoring=scoring, cv=5, return_train_score=True)

{'fit_time': array([0.01299   , 0.00564313, 0.00984812, 0.00682902, 0.00566387]),
 'score_time': array([0.00887132, 0.00666094, 0.01384878, 0.00970411, 0.00985599]),
 'test_accuracy': array([0.6011236 , 0.6741573 , 0.6741573 , 0.71910112, 0.72316384]),
 'train_accuracy': array([0.697609  , 0.67932489, 0.67932489, 0.66807314, 0.66713483]),
 'test_precision': array([0.45454545, 0.60416667, 0.61363636, 0.69565217, 0.72093023]),
 'train_precision': array([0.65745856, 0.63253012, 0.62941176, 0.60714286, 0.60233918]),
 'test_recall': array([0.22058824, 0.42647059, 0.39705882, 0.47058824, 0.45588235]),
 'train_recall': array([0.4375    , 0.38602941, 0.39338235, 0.375     , 0.37867647]),
 'test_roc_auc': array([0.58248663, 0.64772727, 0.70721925, 0.74144385, 0.72517539]),
 'train_roc_auc': array([0.70516632, 0.68855102, 0.67307886, 0.6645744 , 0.66875   ])}

In [17]:
cross_val_score(logreg, X, y, cv=5, scoring='accuracy').mean()

0.6783406335301212

In [18]:
train_set.columns

Index(['PassengerId', 'Survived', 'Pclass', 'Name', 'Sex', 'Age', 'SibSp',
       'Parch', 'Ticket', 'Fare', 'Cabin', 'Embarked'],
      dtype='object')

In [19]:
X = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex']]

In [20]:
X.head()

Pclass     Sex
0       3    male
1       1  female
2       3  female
3       1  female
4       3    male

In [21]:
from sklearn.preprocessing import OneHotEncoder

In [22]:
from sklearn.pipeline import make_pipeline

In [23]:
ohe = OneHotEncoder()

In [24]:
from sklearn.compose import make_column_transformer

In [25]:
column_trans = make_column_transformer(
    (OneHotEncoder(), ['Sex']), 
    remainder='passthrough'
)

In [26]:
pipe = make_pipeline(column_trans, logreg)

In [27]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy').mean()

0.7862756300387227

In [28]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy')

array([0.80337079, 0.80337079, 0.78651685, 0.75280899, 0.78531073])

In [29]:
X = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex', 'Embarked']]

In [30]:
X.head()

Pclass     Sex Embarked
0       3    male        S
1       1  female        C
2       3  female        S
3       1  female        S
4       3    male        S

In [31]:
from sklearn.preprocessing import StandardScaler

In [32]:
column_trans = make_column_transformer(
    (OneHotEncoder(), ['Sex', 'Embarked']),
#     (StandardScaler(), ['Age']),
    remainder='passthrough'
)

In [33]:
pipe = make_pipeline(column_trans, logreg)

In [34]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy')

array([0.76404494, 0.79213483, 0.76966292, 0.75280899, 0.78531073])

In [35]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy').mean()

0.7727924839713071

In [36]:
# seems like accuracy went down by adding Embarked

In [61]:
from collections import Counter

In [37]:
X = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex', 'Fare']]

In [38]:
column_trans = make_column_transformer(
    (OneHotEncoder(), ['Sex']),
    (StandardScaler(), ['Fare']),
    remainder='passthrough'
)

In [39]:
pipe = make_pipeline(column_trans, logreg)

In [40]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy')

array([0.79213483, 0.80337079, 0.76966292, 0.75842697, 0.78531073])

In [41]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy').mean()

0.7817812480162508

In [42]:
# hmm not good, idk

In [43]:
cross_val_score(pipe, X, y, cv=5, scoring='roc_auc')

array([0.80808824, 0.82954545, 0.84993316, 0.84351604, 0.83857258])

In [44]:
X = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex', 'Fare', 'Embarked', 'SibSp']]

In [45]:
column_trans = make_column_transformer(
    (OneHotEncoder(), ['Sex', 'Embarked']),
    (StandardScaler(), ['Fare']),
    remainder='passthrough'
)

In [46]:
X.head()

Pclass     Sex     Fare Embarked  SibSp
0       3    male   7.2500        S      1
1       1  female  71.2833        C      1
2       3  female   7.9250        S      0
3       1  female  53.1000        S      1
4       3    male   8.0500        S      0

In [47]:
pipe = make_pipeline(column_trans, logreg)

In [48]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy')

array([0.78089888, 0.79775281, 0.78089888, 0.7752809 , 0.8079096 ])

In [49]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy').mean()

0.7885482130387862

In [50]:
cross_val_score(pipe, X, y, cv=5, scoring='roc_auc').mean()

0.840671638129814

In [51]:
from sklearn.impute import KNNImputer

In [52]:
X = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex', 'Fare', 'Embarked', 'SibSp', 'Age']]

In [53]:
X.isna().sum()

Pclass        0
Sex           0
Fare          0
Embarked      0
SibSp         0
Age         177
dtype: int64

In [54]:
from sklearn.impute import SimpleImputer

In [55]:
column_trans = make_column_transformer(
    (OneHotEncoder(handle_unknown='ignore'), ['Sex', 'Embarked']),
    (StandardScaler(), ['Fare']),
    (SimpleImputer(strategy='median'), ['Age']),
    remainder='passthrough'
)

In [56]:
pipe = make_pipeline(column_trans, logreg)

In [57]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy').mean()

0.7908144480416428

In [58]:
cross_val_score(pipe, X, y, cv=5, scoring='roc_auc').mean()

0.8494683069224355

In [62]:
Counter(train_set['Parch'])

Counter({0: 678, 1: 118, 2: 80, 5: 5, 3: 5, 4: 4, 6: 1})

In [67]:
X = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex', 'Fare', 'Age', 'Embarked', 'SibSp', 'Parch']]

In [68]:
column_trans = make_column_transformer(
    (OneHotEncoder(handle_unknown='ignore'), ['Sex', 'Embarked']),
    (StandardScaler(), ['Fare']),
    (SimpleImputer(strategy='median'), ['Age']),
    remainder='passthrough'
)

In [69]:
pipe = make_pipeline(column_trans, logreg)

In [70]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy')

array([0.76966292, 0.78651685, 0.78089888, 0.76966292, 0.82485876])

In [71]:
cross_val_score(pipe, X, y, cv=5, scoring='accuracy').mean()

0.786320066019171

In [72]:
cross_val_score(pipe, X, y, cv=5, scoring='roc_auc').mean()

0.8474439483883629

In [73]:
# seems like I should't be adding Parch

In [74]:
X_train = train_set.loc[train_set.Embarked.notna(), ['Pclass', 'Sex', 'Fare', 'Embarked', 'SibSp', 'Age']]

In [85]:
# column_trans = make_column_transformer(
#     (OneHotEncoder(handle_unknown='ignore'), ['Sex', 'Embarked']),
#     (StandardScaler(), ['Fare']),
#     (SimpleImputer(strategy='median'), ['Age']),
#     remainder='passthrough'
# )

In [86]:
from sklearn.compose import ColumnTransformer

In [87]:
column_trans = ColumnTransformer([
    ('ohe', OneHotEncoder(handle_unknown='ignore'), ['Sex', 'Embarked']),
    ('scaler', StandardScaler(), ['Fare']), 
    ('imputer', SimpleImputer(strategy='median'), ['Age'])],
    remainder='passthrough')

In [88]:
from sklearn.pipeline import Pipeline

In [89]:
pipe = Pipeline([
    ('preprocessor', column_trans),
    ('classifier', LogisticRegression(solver='lbfgs', max_iter=10000))
])

In [84]:
# pipe = make_pipeline(column_trans, logreg)

In [91]:
cross_val_score(pipe, X_train, y, cv=5, scoring='accuracy').mean()

0.7908144480416428

In [92]:
cross_val_score(pipe, X_train, y, cv=5, scoring='roc_auc').mean()

0.8494683069224355

In [93]:
# importing all classifiers
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
# from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

In [99]:
param_grid = [
    {'classifier' : [LogisticRegression()],
     'classifier__penalty' : ['l1', 'l2'],
    'classifier__C' : np.logspace(-4, 4, 20),
    'classifier__solver' : ['liblinear']},
]

In [113]:
grid_search = GridSearchCV(pipe, param_grid, cv=5, scoring=scoring, return_train_score=True, refit='roc_auc')

In [114]:
grid_search.fit(X_train, y)

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

...

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/pipeline.py", line 335, in fit
    self._final_estimator.fit(Xt, y, **fit_params_last_step)
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/ensemble/_forest.py", line 392, in fit
    for i, t in enumerate(trees))
  File "/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/joblib/parallel.py", line 1004, in __call__
    if self.dispatch_one_batch(iterator):
  File "/Users/kalyaniasthana/opt/anaconda3/lib/pytho

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocessor',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('ohe',
                                                                         OneHotEncoder(handle_unknown='ignore'),
                                                                         ['Sex',
                                                                          'Embarked']),
                                                                        ('scaler',
                                                                         StandardScaler(),
                                                                         ['Fare']),
                                                                        ('imputer',
                                                                         SimpleImputer(strategy='median'),
                               

In [115]:
grid_search.best_score_

0.8725826669283228

In [112]:
param_grid = [
    {'classifier' : [RandomForestClassifier()],
    'classifier__n_estimators' : list(range(10,101,10)),
    'classifier__bootstrap': [True, False],
    'classifier__max_depth': list(range(10, 10, 110)) + [None],
    'classifier__min_samples_leaf': list(range(2,8)),
    'classifier__max_features' : list(range(6,32,5))},
]

In [119]:
param_grid = [
    {'classifier' : [MLPClassifier()],
    'classifier__hidden_layer_sizes' : [(10,20,10), (20, ), (10,30,10)],
    'classifier__activation': ['tanh', 'relu'],
    'classifier__solver': ['sgd', 'adam'],
    'classifier__alpha': [0.01, 0.05, 0.015],
    'classifier__learning_rate' : ['constant', 'adaptive'],
    'preprocessor__imputer__strategy': ['mean', 'median']}
]

In [120]:
grid_search = GridSearchCV(pipe, param_grid, cv=5, scoring=scoring, return_train_score=True, refit='roc_auc')

In [121]:
grid_search.fit(X_train, y)

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precis

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

...

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1221: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multila

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/Users/kalyaniasthana/opt/anaconda3/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:585: ConvergenceWarning: Stochastic Optimizer: Maximum iterati

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocessor',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('ohe',
                                                                         OneHotEncoder(handle_unknown='ignore'),
                                                                         ['Sex',
                                                                          'Embarked']),
                                                                        ('scaler',
                                                                         StandardScaler(),
                                                                         ['Fare']),
                                                                        ('imputer',
                                                                         SimpleImputer(strategy='median'),
                               

In [122]:
grid_search.best_score_

0.8680372123828681

In [135]:
grid_search.cv_results_['mean_test_accuracy'][grid_search.best_index_]

0.8054402336062972

In [136]:
param_grid = [
    {'classifier' : [KNeighborsClassifier()],
    'classifier__n_neighbors' : [3, 5, 11, 19],
    'classifier__weights': ['uniform', 'distance'],
    'classifier__metric': ['euclidean', 'manhattan'],
    'preprocessor__imputer__strategy': ['mean', 'median']}
]

In [139]:
grid_search = GridSearchCV(pipe, param_grid, cv=5, scoring=scoring, return_train_score=True, refit='roc_auc')

In [140]:
grid_search.fit(X_train, y)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocessor',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('ohe',
                                                                         OneHotEncoder(handle_unknown='ignore'),
                                                                         ['Sex',
                                                                          'Embarked']),
                                                                        ('scaler',
                                                                         StandardScaler(),
                                                                         ['Fare']),
                                                                        ('imputer',
                                                                         SimpleImputer(strategy='median'),
                               

In [141]:
grid_search.best_score_

0.8466565274984056

In [142]:
grid_search.cv_results_['mean_test_accuracy'][grid_search.best_index_]

0.8020440551006158

In [147]:
param_grid = [
    {'classifier' : [SVC()],
    'classifier__kernel' : ['linear', 'poly', 'rbf'],
    'classifier__gamma': [1, 0.1, 0.01, 0.001],
    'classifier__random_state': [42],
    'classifier__C': [0.1, 1, 10, 100, 1000],
    'preprocessor__imputer__strategy': ['mean', 'median']}
]

In [148]:
grid_search = GridSearchCV(pipe, param_grid, cv=5, scoring=scoring, return_train_score=True, refit='roc_auc')